# Test Huggingface Save/Load Workflow

In [1]:
import jax
import flax.nnx as nnx
import jax.numpy as jnp

from jaxpt.models.mobile_llm import Mobile_LLM, MobileLLM_Config, convert_to_hf, from_hf_pretrained

key = jax.random.PRNGKey(1337)
rngs = nnx.Rngs(key)
config = MobileLLM_Config(dtype=jnp.float32, \
                    vocab_size=49152,
                    n_embed=576,
                    n_head=9,
                    n_kv_head=3,
                    n_mlp_hidden=1536,
                    sdpa_implementation="xla")
                    

#hf_m.save_pretrained("/Users/vikram/dev/jaxpt/notebooks/mobile_llm.hf")


In [2]:

#m = Mobile_LLM(config, rngs)
#graphdef, params, state = nnx.split(m, nnx.Param, ...)
#nnx.display(params)
#hf_m = convert_to_hf(m)
#hf_state = hf_m.state_dict()

In [3]:
from jaxpt.models.mobile_llm import from_hf_pretrained,load_hf_pretrained
m = from_hf_pretrained(config, rngs)
graphdef, params, other_state = nnx.split(m, nnx.Param, ...)
nnx.display(params)
hf_m = load_hf_pretrained()
print(hf_m.model)

LlamaModel(
  (embed_tokens): Embedding(49152, 576)
  (layers): ModuleList(
    (0-29): 30 x LlamaDecoderLayer(
      (self_attn): LlamaAttention(
        (q_proj): Linear(in_features=576, out_features=576, bias=False)
        (k_proj): Linear(in_features=576, out_features=192, bias=False)
        (v_proj): Linear(in_features=576, out_features=192, bias=False)
        (o_proj): Linear(in_features=576, out_features=576, bias=False)
      )
      (mlp): LlamaMLP(
        (gate_proj): Linear(in_features=576, out_features=1536, bias=False)
        (up_proj): Linear(in_features=576, out_features=1536, bias=False)
        (down_proj): Linear(in_features=1536, out_features=576, bias=False)
        (act_fn): SiLU()
      )
      (input_layernorm): LlamaRMSNorm((576,), eps=1e-05)
      (post_attention_layernorm): LlamaRMSNorm((576,), eps=1e-05)
    )
  )
  (norm): LlamaRMSNorm((576,), eps=1e-05)
  (rotary_emb): LlamaRotaryEmbedding()
)


In [4]:
import torch.nn as nn

class IdentityLayer(nn.Module):
    def forward(self, hidden_states, *args, **kwargs):
        return hidden_states.unsqueeze(0)

class IdentityAttn(nn.Module):
    def forward(self, hidden_states, *args, **kwargs):
        return hidden_states.unsqueeze(0), None

class ZeroRotation(nn.Module):
    def forward(self, hidden_states, *args, **kwargs):
        out_shape = hidden_states[:, :, :64].shape
        print(out_shape)
        return torch.tensor(np.ones(out_shape)), torch.tensor(np.zeros(out_shape))

#for i in range(len(hf_m.model.layers)):
#    if i > 1:
#        hf_m.model.layers[i] = IdentityLayer() 
    #else:
        #hf_m.model.layers[i].self_attn = IdentityAttn()
        #hf_m.model.layers[i].mlp = IdentityLayer()
        #hf_m.model.layers[i].input_layernorm = IdentityLayer()
        #hf_m.model.layers[i].post_attention_layernorm = IdentityLayer()
#hf_m.model.norm = IdentityLayer() 
#hf_m.model.rotary_emb = ZeroRotation()
#hf_m.lm_head = IdentityLayer()
#hf_m.model.embed_tokens = None

#for i in range(len(m.h)):
#    if i > 1:
#        m.h[i] = lambda x: x
    #else:
        #m.h[i].attn = lambda x: x
        #m.h[i].mlp = lambda x: x
        #m.h[i].rms_n_1 = lambda x: x
        #m.h[i].rms_n_2 = lambda x: x
#m.rms_n_f = lambda x: x

In [5]:
nnx.display(m)
print(hf_m)

LlamaForCausalLM(
  (model): LlamaModel(
    (embed_tokens): Embedding(49152, 576)
    (layers): ModuleList(
      (0-29): 30 x LlamaDecoderLayer(
        (self_attn): LlamaAttention(
          (q_proj): Linear(in_features=576, out_features=576, bias=False)
          (k_proj): Linear(in_features=576, out_features=192, bias=False)
          (v_proj): Linear(in_features=576, out_features=192, bias=False)
          (o_proj): Linear(in_features=576, out_features=576, bias=False)
        )
        (mlp): LlamaMLP(
          (gate_proj): Linear(in_features=576, out_features=1536, bias=False)
          (up_proj): Linear(in_features=576, out_features=1536, bias=False)
          (down_proj): Linear(in_features=1536, out_features=576, bias=False)
          (act_fn): SiLU()
        )
        (input_layernorm): LlamaRMSNorm((576,), eps=1e-05)
        (post_attention_layernorm): LlamaRMSNorm((576,), eps=1e-05)
      )
    )
    (norm): LlamaRMSNorm((576,), eps=1e-05)
    (rotary_emb): LlamaRotaryEm

In [6]:
import torch
import numpy as np


m.eval()
hf_m.eval()

with torch.no_grad():
    x = jax.random.randint(jax.random.key(1337), shape=(4, 10), minval=0, maxval=config.vocab_size)
    y_flax = m(x)
    #y_flax = m.wte(x)
    #y_flax = m.wte.attend(y_flax)
    y_flax = np.array(y_flax)
    x = torch.tensor(np.array(x))
    #y_hf = hf_m.model.embed_tokens(x)
    #print(y_hf.shape)
    #y_hf = hf_m.lm_head(y_hf)
    y_hf = hf_m(x)
    y_hf = y_hf.logits.detach().numpy()
    #y_hf = y_hf.detach().numpy()

print(np.mean(y_flax[:, :, :]))
print(np.mean(y_hf[:, :, :]))

2.7903364
2.790339
